In [1]:
import pandas as pd
plan = pd.read_csv("5_1_time_plan.csv")
phase = pd.read_csv('2_phase_info.csv')
plan = plan[plan.ID<5]
ID2starttime = {1:"00:00", 2:"07:00", 3:"09:00", 4:"18:30"}
plan['start_hour'] = plan.ID.apply(lambda id:ID2starttime[id].split(":")[0])
plan['start_minute']=plan.ID.apply(lambda id:ID2starttime[id].split(":")[1])
plan = plan[['inter_no', 'start_hour', 'start_minute', 'phase_no', 'ring_type', 'duration']]
plan = pd.merge(plan, phase[['inter_no', 'phase_no', 'ring_type', 'flow_no']], on=['inter_no', 'phase_no', 'ring_type'], how='left')
plan['flow_no'] = plan['flow_no'].fillna(18).astype(int)
plan

inter_no start_hour start_minute  phase_no ring_type  duration  flow_no
0         175         00           00         1         A        37        8
1         175         00           00         1         B        37        4
2         175         00           00         2         A        39        7
3         175         00           00         2         B        39        3
4         175         00           00         3         A        55        6
..        ...        ...          ...       ...       ...       ...      ...
267       212         09           00         2         B       171       18
268       212         18           30         1         A        39        6
269       212         18           30         1         B        39        2
270       212         18           30         2         A       171       17
271       212         18           30         2         B       171       18

[272 rows x 7 columns]

In [ ]:
# with pd.option_context('display.max_rows', None, 'display.max_columns', None):
#     display(plan)

In [ ]:
print(sorted(plan.inter_no.unique()))
print(list(ID2starttime.values()))
display(plan[:20])

In [ ]:
A = {index:group for index, group in plan.groupby(['inter_no', 'start_hour', 'start_minute', 'ring_type'])}
L = list(A.values())
S = pd.Series([list(A.values())[i].duration.sum() % 10 != 0 for i in range(len(L))])
S[S]

In [2]:
plans = {index:group for index, group in plan.groupby(['inter_no', 'start_hour', 'start_minute'])}
keys = list(plans.keys())

In [ ]:
df = plans[keys[0]].copy()
df.reset_index(inplace=True)
display(df)
df = df.pivot_table(index=['inter_no', 'start_hour', 'start_minute', 'phase_no'],
                                columns='ring_type',
                                values=['duration', 'flow_no'],
                                aggfunc='first').reset_index()

# Renaming the columns for clarity
df.columns = ['inter_no', 'start_hour', 'start_minute', 'phase_no', 'dura_A', 'dura_B', 'move_A', 'move_B']
df

In [3]:
trans175 = [key[1:3] for key in keys if key[0]==175]
trans175

[('00', '00'), ('07', '00'), ('09', '00'), ('18', '30')]

In [ ]:
for hhmm in trans175:
    hh = hhmm[0]
    mm = hhmm[1]
    print(hh)
    print(mm)

In [4]:
hhmm = trans175[0]
df = plans[(175,hhmm[0],hhmm[1])].copy()
display(df)
df = df.pivot_table(index=['inter_no', 'start_hour', 'start_minute', 'phase_no'],
                                columns='ring_type',
                                values=['duration', 'flow_no'],
                                aggfunc='first').reset_index()
df.columns = ['inter_no', 'start_hour', 'start_minute', 'phase_no', 'dura_A', 'dura_B', 'move_A', 'move_B']
df

inter_no start_hour start_minute  phase_no ring_type  duration  flow_no
0       175         00           00         1         A        37        8
1       175         00           00         1         B        37        4
2       175         00           00         2         A        39        7
3       175         00           00         2         B        39        3
4       175         00           00         3         A        55        6
5       175         00           00         3         B        25        1
6       175         00           00         4         A        29        5
7       175         00           00         4         B        59        2

inter_no start_hour start_minute  phase_no  dura_A  dura_B  move_A  move_B
0       175         00           00         1      37      37       8       4
1       175         00           00         2      39      39       7       3
2       175         00           00         3      55      25       6       1
3       175         00           00         4      29      59       5       2

In [9]:
for i in range(1,len(trans175)):
    print(i)

1
2
3


In [11]:
from datetime import datetime
move = pd.DataFrame()
now = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
for i in range(1,len(trans175)):
    print(i)
    hhmm = trans175[i]
    df = plans[(175,hhmm[0],hhmm[1])].copy()
    df = df.pivot_table(index=['inter_no', 'start_hour', 'start_minute', 'phase_no'],
                                    columns='ring_type',
                                    values=['duration', 'flow_no'],
                                    aggfunc='first').reset_index()
    df.columns = ['inter_no', 'start_hour', 'start_minute', 'phase_no', 'dura_A', 'dura_B', 'move_A', 'move_B']

    trans = int(datetime(2024, 1, 5, int(hhmm[0]), int(hhmm[1]), 0).timestamp())
    cycle = df.dura_A.sum()

    while True:
        A_phas = []
        B_phas = []
        A_move = []
        B_move = []
        for _, row in df.iterrows():
            A_phas += [row['phase_no']] * row['dura_A']
            B_phas += [row['phase_no']] * row['dura_B']
            A_move += [row['move_A']] * row['dura_A']
            B_move += [row['move_B']] * row['dura_B']
        unix_time = range(now, now + cycle)
        inter_no = list(df.inter_no.unique()) * cycle
        move = pd.concat([move, pd.DataFrame({'inter_no':inter_no, 'unix_time':unix_time, 'A_phas':A_phas, 'B_phas':B_phas, 'A_move':A_move, 'B_move':B_move})])
        now += cycle
        if now > trans:
            break
    move

1
2
3


In [12]:
len(move)

66720

In [15]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(move[:10000])

inter_no   unix_time  A_phas  B_phas  A_move  B_move
0         175  1704380400       1       1       8       4
1         175  1704380401       1       1       8       4
2         175  1704380402       1       1       8       4
3         175  1704380403       1       1       8       4
4         175  1704380404       1       1       8       4
5         175  1704380405       1       1       8       4
6         175  1704380406       1       1       8       4
7         175  1704380407       1       1       8       4
8         175  1704380408       1       1       8       4
9         175  1704380409       1       1       8       4
10        175  1704380410       1       1       8       4
11        175  1704380411       1       1       8       4
12        175  1704380412       1       1       8       4
13        175  1704380413       1       1       8       4
14        175  1704380414       1       1       8       4
15        175  1704380415       1       1       8       4
16        175  1704380416       1       1       8       4
17        175  1704380417       1       1       8       4
18        175  1704380418       1       1       8       4
19        175  1704380419       1       1       8       4
20        175  1704380420       1       1       8       4
21        175  1704380421       1       1       8       4
22        175  1704380422       1       1       8       4
23        175  1704380423       1       1       8       4
24        175  1704380424       1       1       8       4
25        175  1704380425       1       1       8       4
26        175  1704380426       1       1       8       4
27        175  1704380427       1       1       8       4
28        175  1704380428       1       1       8       4
29        175  1704380429       1       1       8       4
30        175  1704380430       1       1       8       4
31        175  1704380431       1       1       8       4
32        175  1704380432       1       1       8       4
33        175  1704380433       1       1       8       4
34        175  1704380434       1       1       8       4
35        175  1704380435       1       1       8       4
36        175  1704380436       1       1       8       4
37        175  1704380437       2       2       7       3
38        175  1704380438       2       2       7       3
39        175  1704380439       2       2       7       3
40        175  1704380440       2       2       7       3
41        175  1704380441       2       2       7       3
42        175  1704380442       2       2       7       3
43        175  1704380443       2       2       7       3
44        175  1704380444       2       2       7       3
45        175  1704380445       2       2       7       3
46        175  1704380446       2       2       7       3
47        175  1704380447       2       2       7       3
48        175  1704380448       2       2       7       3
49        175  1704380449       2       2       7       3
50        175  1704380450       2       2       7       3
51        175  1704380451       2       2       7       3
52        175  1704380452       2       2       7       3
53        175  1704380453       2       2       7       3
54        175  1704380454       2       2       7       3
55        175  1704380455       2       2       7       3
56        175  1704380456       2       2       7       3
57        175  1704380457       2       2       7       3
58        175  1704380458       2       2       7       3
59        175  1704380459       2       2       7       3
60        175  1704380460       2       2       7       3
61        175  1704380461       2       2       7       3
62        175  1704380462       2       2       7       3
63        175  1704380463       2       2       7       3
64        175  1704380464       2       2       7       3
65        175  1704380465       2       2       7       3
66        175  1704380466       2       2       7       3
67        175  1704380467       2       2       7       3
68 

In [23]:
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
print(midnight + 7*60*60)

1704405600


In [ ]:
move.unix_time.max()
datetime.fromtimestamp(move.unix_time.max())

In [ ]:
from datetime import datetime
move_cols = ['inter_no', 'unix_time', 'A_phas', 'B_phas', 'A_move', 'B_move']
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
move = pd.DataFrame(columns = move_cols)
for i in range(37):
    move.loc[i] = pd.Series(dict(zip(move_cols,[175, midnight+i, 1, 1, 8, 4])))
for i in range(37,37+39):
    move.loc[i] = pd.Series(dict(zip(move_cols,[175, midnight+37+i, 2, 2, 7, 3])))
move[:60]